In [1]:
using Revise;
includet("../experiment/ringworld.jl")

┌ Info: Precompiling ActionRNNs [8317d1c6-c5c3-11e9-1282-0f8c4be94ea0]
└ @ Base loading.jl:1260


In [2]:
using Statistics, Plots, RollingFunctions, ActionRNNs, Flux
import Random

In [3]:
RWU = ActionRNNs.RingWorldUtils

ActionRNNs.RingWorldUtils

In [4]:
function construct_agent(outhorde, fc, rnn, opt, τ)


    fs = MinimalRLCore.feature_size(fc)
    
    ap = ActionRNNs.RandomActingPolicy([0.5, 0.5])

    ActionRNNs.PredERAgent(outhorde,
                           rnn,
                           opt,
                           τ,
                           fc,
                           fs,
                           1, 
                           1, τ, 1, #Replay details
                           ap)
end


construct_agent (generic function with 1 method)

In [15]:
fc = RWU.OneHotFeatureCreator()
fs = MinimalRLCore.feature_size(fc)
num_hidden = 12
outhorde = RWU.gammas_term(0.0:0.1:0.9)

Random.seed!(10392)

rnn = Chain(
    GRU(fs, num_hidden), 
#     Dense(num_hidden, num_hidden, relu),
    Dense(num_hidden, length(outhorde)))
opt = RMSProp(0.0005)
τ = 5

agent = construct_agent(outhorde, fc, rnn, opt, τ)
env = RingWorld(6)

out_pred, out_err, out_loss = RingWorldExperiment.experiment_loop(env, agent, "gammas_term", 300000, Random.GLOBAL_RNG; prgs=true)

Float32[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Float32


Step: 100%|█████████████████████████████████████████████| Time: 0:02:00


(Float32[-0.2313003 0.6035461 … -0.5385567 0.09323313; -0.75148207 1.2057681 … -0.19761041 0.714937; … ; 1.0050013 1.0027074 … 0.41284725 0.6595514; -0.043359935 0.064142734 … 0.52851534 0.7532853], Float32[-1.2313004 -0.39645392 … -0.9481567 -0.56286687; -0.75148207 1.2057672 … -0.4597544 0.18349597; … ; 0.0050013065 0.0027073622 … 0.0032472508 0.003451382; -0.043359935 -0.035857268 … 0.016515339 0.024285289], Float32[0.0, 0.0, 0.0, 0.0, 0.02418949, 0.8233431, 0.057072688, 0.07384216, 0.09378667, 0.120154224  …  1.5546537f-5, 5.2844232f-5, 9.977532f-6, 1.417274f-6, 0.00016519833, 2.1717883f-6, 5.263187f-5, 1.2286101f-5, 7.1271993f-6, 1.9436082f-5])

In [16]:
plot(rollmean(sqrt.(mean(out_err.^2; dims=2))[:,1], 1000))

In [12]:
 out_pred

300000×2 Array{Float32,2}:
 -0.810127  -0.446337
 -0.194085   0.610705
 -0.745484  -0.198224
 -0.78609    1.03833
 -1.31298   -0.37334
 -1.33271    0.229872
 -1.02758   -0.659092
 -0.268407   0.400788
 -0.599667   0.023415
 -0.44621    0.732368
 -0.637332  -0.350381
 -0.731698   1.52091
 -1.33967    0.224559
  ⋮         
  0.788867   0.803954
  0.760382   0.871779
  0.714983   0.91357
  0.675788   0.931759
  0.573635   0.58815
  0.648051   0.984082
  0.561955   0.60433
  1.05016    0.655184
  0.588787   0.568801
  0.995209   0.649302
  0.966887   0.719737
  0.817133   0.790765

In [13]:
 out_pred .- out_err

300000×2 Array{Float32,2}:
 0.531441  0.531441
 0.6561    1.0
 0.531441  0.531441
 1.0       0.6561
 0.9       0.729
 1.0       0.6561
 0.531441  0.531441
 0.6561    1.0
 0.531441  0.531441
 0.6561    1.0
 0.729     0.9
 0.6561    1.0
 0.729     0.9
 ⋮         
 0.9       0.729
 0.81      0.81
 0.729     0.9
 0.6561    1.0
 0.531441  0.531441
 0.6561    1.0
 0.531441  0.531441
 1.0       0.6561
 0.531441  0.531441
 1.0       0.6561
 0.9       0.729
 0.81      0.81